In [1]:
import os,sys
from collections import defaultdict
import posixpath
from elftools.elf.elffile import ELFFile
from capstone import *






filePath = '/home/nahid/reverse/binaries/gnuit/src/gitfm'
fh = open(filePath, 'rb')
bin_bytearray = bytearray(fh.read())









In [2]:


with open(filePath, 'rb') as f:
    elffile = ELFFile(f)

    entry_point = elffile._parse_elf_header().e_entry
    segment_load_address = elffile.get_segment(0).header.p_vaddr
    entry_offset = entry_point - segment_load_address


        
print(entry_point , segment_load_address,entry_offset)

20208 64 20144


In [3]:



lineprogram_addresses = []

with open(filePath, 'rb') as f:
    elffile = ELFFile(f)
    
    


    text_section = elffile.get_section_by_name(".text")
    textSectionLen = len(bin_bytearray)
    textSectionStart = text_section.header.sh_addr
    textSectionEnd = textSectionStart + textSectionLen
    program_entry_point = elffile._parse_elf_header().e_entry
    

    
    
    if not elffile.has_dwarf_info():
        print('  file has no DWARF info')
        

    dwarfinfo = elffile.get_dwarf_info()
    

    cc = 0
    for CU in dwarfinfo.iter_CUs():
        print('  Found a compile unit at offset %s, length %s' % (
            CU.cu_offset, CU['unit_length']))

        # Every compilation unit in the DWARF information may or may not
        # have a corresponding line program in .debug_line.
        line_program = dwarfinfo.line_program_for_CU(CU)
        if line_program is None:
            print('  DWARF info is missing a line program for this CU')
            continue
        for le in line_program.get_entries():
            if le.state is not None:
                lineprogram_addresses.append(le.state.address)

  Found a compile unit at offset 0, length 10410
  Found a compile unit at offset 10414, length 7795
  Found a compile unit at offset 18213, length 931
  Found a compile unit at offset 19148, length 3815
  Found a compile unit at offset 22967, length 1824
  Found a compile unit at offset 24795, length 15615
  Found a compile unit at offset 40414, length 3379
  Found a compile unit at offset 43797, length 1585
  Found a compile unit at offset 45386, length 4279
  Found a compile unit at offset 49669, length 1102
  Found a compile unit at offset 50775, length 249
  Found a compile unit at offset 51028, length 1910
  Found a compile unit at offset 52942, length 710
  Found a compile unit at offset 53656, length 1720
  Found a compile unit at offset 55380, length 1383
  Found a compile unit at offset 56767, length 5736
  Found a compile unit at offset 62507, length 684
  Found a compile unit at offset 63195, length 4327
  Found a compile unit at offset 67526, length 1936
  Found a compile 

In [4]:
JUMP_OPCODES = ['JO','JNO','JS','JNS','JE','JZ','JNE','JNZ','JB','JNAE','JC','JNB','JAE','JNC','JBE','JNA','JA',
'JNBE','JL','JNGE','JGE','JNL','JLE','JNG','JG','JNLE','JP','JPE','JNP','JPO','JCXZ','JECXZ']


#took inspiration from capstone github sample code 





textSectionEnd = textSectionStart+textSectionLen


md = Cs(CS_ARCH_X86, CS_MODE_64)


visited_addresses = []
entry_addresses = []
address_and_instructions = {}

entry_addresses.append(program_entry_point)
entry_addresses += lineprogram_addresses
counter = 0


call_addresses = []
while len(entry_addresses)>0 :
    
    
    print('ENTRIES REMAINING',len(entry_addresses))
    current_entry_address = entry_addresses.pop(0)
    
    if current_entry_address in visited_addresses:
        continue
    

    CODE = bin_bytearray[current_entry_address: textSectionEnd]
    if len(CODE)==0:
        continue
    for i in md.disasm(CODE, current_entry_address):

        print("0x%x:\t%s\t%s \t%s" %(i.address, i.mnemonic, i.op_str ,i.size))  
        

        address_and_instructions[i.address] = i
        
        visited_addresses.append(i.address)

        # IF there is a conditional jump
        if i.mnemonic.upper() in JUMP_OPCODES:
            try:
                if int(i.op_str,0)>=0:
                    if i.op_str not in visited_addresses:
                        print("\t\t\t> %s" %( i.op_str  ))  
                        
                        print('->',hex(i.address + i.size),(i.address + i.size),(i.op_str,0) )
                        entry_addresses.append(int(i.address + i.size))
                        entry_addresses.append(int(i.op_str,0))
                break
            except: 
                print('\t\t->->->                               indirect BRUNCH')
                break
        
        #direct jump  TODO: check all versions
        if i.mnemonic.upper() in ['JMP']: #TODO handle JMP 0xACDC:0x5578
            print(i.op_str)
            try:
                if int(i.op_str,0)>=0:
                    
                    if int(i.op_str,0)>=textSectionStart and int(i.op_str,0)<=textSectionEnd:
                        entry_addresses.append(int(i.op_str,0))
                break
                    
                    
            except:
                print('\t\t->->->                                  indirect JMP')
                break
        if i.mnemonic.upper() in ['RET', 'LEAVE']:
#             end of basic block
            break
#         TODO: check all versions
        if i.mnemonic.upper() in ["CALL"]:
            try:
                if int(i.op_str,0) >= 0:
                    call_addr = int(i.op_str,0)
                    print(call_addr, textSectionStart,textSectionEnd )
                    if call_addr <textSectionStart or call_addr>textSectionEnd:
                        print("EXIT"*10)
                    else:
                        print("YYYY"*10)
                        call_addresses.append(call_addr)
            except:
                
                break
                

ENTRIES REMAINING 13617
0x4ef0:	endbr64	 	4
0x4ef4:	xor	ebp, ebp 	2
0x4ef6:	mov	r9, rdx 	3
0x4ef9:	pop	rsi 	1
0x4efa:	mov	rdx, rsp 	3
0x4efd:	and	rsp, 0xfffffffffffffff0 	4
0x4f01:	push	rax 	1
0x4f02:	push	rsp 	1
0x4f03:	xor	r8d, r8d 	3
0x4f06:	xor	ecx, ecx 	2
0x4f08:	lea	rdi, [rip + 0x28fb] 	7
0x4f0f:	call	qword ptr [rip + 0x2a0a3] 	6
ENTRIES REMAINING 13616
0x4fd9:	endbr64	 	4
0x4fdd:	push	rbp 	1
0x4fde:	mov	rbp, rsp 	3
0x4fe1:	mov	eax, dword ptr [rip + 0x2b9f5] 	6
0x4fe7:	cmp	eax, 6 	3
0x4fea:	jle	0x501a 	2
			> 0x501a
-> 0x4fec 20460 ('0x501a', 0)
ENTRIES REMAINING 13617
ENTRIES REMAINING 13616
ENTRIES REMAINING 13615
0x4fec:	mov	eax, dword ptr [rip + 0x2a036] 	6
0x4ff2:	test	eax, eax 	2
0x4ff4:	je	0x5008 	2
			> 0x5008
-> 0x4ff6 20470 ('0x5008', 0)
ENTRIES REMAINING 13616
ENTRIES REMAINING 13615
0x4ff6:	mov	eax, dword ptr [rip + 0x2b9e4] 	6
0x4ffc:	cmp	eax, 0xb 	3
0x4fff:	jle	0x501a 	2
			> 0x501a
-> 0x5001 20481 ('0x501a', 0)
ENTRIES REMAINING 13616
ENTRIES REMAINING 13615
0x5001

ENTRIES REMAINING 13576
ENTRIES REMAINING 13575
ENTRIES REMAINING 13574
ENTRIES REMAINING 13573
0x531a:	mov	eax, dword ptr [rip + 0x2b6c0] 	6
0x5320:	cdqe	 	2
0x5322:	jmp	0x5329 	2
0x5329
ENTRIES REMAINING 13573
ENTRIES REMAINING 13572
0x5324:	mov	eax, 0 	5
0x5329:	mov	rsi, rdx 	3
0x532c:	mov	rdi, rax 	3
0x532f:	call	0x10167 	5
65895 20192 449736
YYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYY
0x5334:	mov	eax, dword ptr [rip + 0x2b6a2] 	6
0x533a:	cmp	eax, 1 	3
0x533d:	je	0x534a 	2
			> 0x534a
-> 0x533f 21311 ('0x534a', 0)
ENTRIES REMAINING 13573
ENTRIES REMAINING 13572
ENTRIES REMAINING 13571
ENTRIES REMAINING 13570
0x533f:	mov	eax, dword ptr [rip + 0x2b697] 	6
0x5345:	lea	edx, [rax - 2] 	3
0x5348:	jmp	0x534f 	2
0x534f
ENTRIES REMAINING 13570
ENTRIES REMAINING 13569
0x534a:	mov	edx, 0 	5
0x534f:	mov	eax, dword ptr [rip + 0x2b68b] 	6
0x5355:	mov	esi, edx 	2
0x5357:	mov	edi, eax 	2
0x5359:	call	0xe1a9 	5
57769 20192 449736
YYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYY
0x535e:	jmp	0x5361 	2
0x5361
EN

0x55ab:	mov	eax, 0 	5
0x55b0:	call	0x10857 	5
67671 20192 449736
YYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYY
0x55b5:	mov	eax, 0 	5
0x55ba:	call	0xf768 	5
63336 20192 449736
YYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYY
0x55bf:	mov	eax, 0 	5
0x55c4:	call	0xb4b7 	5
46263 20192 449736
YYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYY
0x55c9:	nop	 	1
0x55ca:	leave	 	1
ENTRIES REMAINING 13535
ENTRIES REMAINING 13534
ENTRIES REMAINING 13533
ENTRIES REMAINING 13532
0x55cc:	endbr64	 	4
0x55d0:	push	rbp 	1
0x55d1:	mov	rbp, rsp 	3
0x55d4:	sub	rsp, 0x20 	4
0x55d8:	mov	qword ptr [rbp - 0x18], rdi 	4
0x55dc:	mov	qword ptr [rbp - 0x20], rsi 	4
0x55e0:	mov	rax, qword ptr fs:[0x28] 	9
0x55e9:	mov	qword ptr [rbp - 8], rax 	4
0x55ed:	xor	eax, eax 	2
0x55ef:	lea	rcx, [rbp - 0x10] 	4
0x55f3:	mov	rax, qword ptr [rbp - 0x18] 	4
0x55f7:	mov	edx, 1 	5
0x55fc:	mov	rsi, rcx 	3
0x55ff:	mov	rdi, rax 	3
0x5602:	call	0x1f4b1 	5
128177 20192 449736
YYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYY
0x5607:	test	rax, rax 	3
0x560a:	je	0x5623 	

0x5865:	mov	eax, 0 	5
0x586a:	call	0xef64 	5
61284 20192 449736
YYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYY
0x586f:	jmp	0x597f 	5
0x597f
ENTRIES REMAINING 13509
ENTRIES REMAINING 13508
0x5874:	mov	eax, dword ptr [rbp - 8] 	3
0x5877:	and	eax, 1 	3
0x587a:	test	eax, eax 	2
0x587c:	je	0x5982 	6
			> 0x5982
-> 0x5882 22658 ('0x5982', 0)
ENTRIES REMAINING 13509
ENTRIES REMAINING 13508
0x5882:	mov	eax, 0 	5
0x5887:	call	0xf009 	5
61449 20192 449736
YYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYY
0x588c:	jmp	0x5982 	5
0x5982
ENTRIES REMAINING 13508
ENTRIES REMAINING 13507
0x5891:	mov	eax, dword ptr [rbp - 8] 	3
0x5894:	and	eax, 1 	3
0x5897:	test	eax, eax 	2
0x5899:	je	0x5985 	6
			> 0x5985
-> 0x589f 22687 ('0x5985', 0)
ENTRIES REMAINING 13508
ENTRIES REMAINING 13507
0x589f:	mov	eax, 0 	5
0x58a4:	call	0xf0af 	5
61615 20192 449736
YYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYY
0x58a9:	jmp	0x5985 	5
0x5985
ENTRIES REMAINING 13507
ENTRIES REMAINING 13506
0x58ae:	mov	eax, dword ptr [rbp - 8] 	3
0x58b1:	and	eax, 1

0x5ad3:	mov	eax, dword ptr [rbp - 0x14] 	3
0x5ad6:	movsxd	rdx, eax 	3
0x5ad9:	mov	rax, qword ptr [rbp - 0x10] 	4
0x5add:	add	rax, rdx 	3
0x5ae0:	mov	byte ptr [rax], 0 	3
0x5ae3:	mov	rax, qword ptr [rbp - 0x10] 	4
0x5ae7:	leave	 	1
ENTRIES REMAINING 13478
ENTRIES REMAINING 13477
ENTRIES REMAINING 13476
ENTRIES REMAINING 13475
0x5ae9:	endbr64	 	4
0x5aed:	push	rbp 	1
0x5aee:	mov	rbp, rsp 	3
0x5af1:	sub	rsp, 0x30 	4
0x5af5:	mov	qword ptr [rbp - 0x28], rdi 	4
0x5af9:	mov	qword ptr [rbp - 0x18], 0 	8
0x5b01:	mov	rax, qword ptr [rbp - 0x28] 	4
0x5b05:	mov	qword ptr [rbp - 0x10], rax 	4
0x5b09:	mov	rax, qword ptr [rbp - 0x28] 	4
0x5b0d:	mov	rdi, rax 	3
0x5b10:	call	0x4960 	5
18784 20192 449736
EXITEXITEXITEXITEXITEXITEXITEXITEXITEXIT
0x5b15:	mov	rdx, rax 	3
0x5b18:	mov	rax, rdx 	3
0x5b1b:	add	rax, rax 	3
0x5b1e:	add	rax, rdx 	3
0x5b21:	add	rax, 9 	4
0x5b25:	mov	rdi, rax 	3
0x5b28:	call	0x24650 	5
149072 20192 449736
YYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYYY
0x5b2d:	mov	qword ptr [rbp - 8], rax 

...

0x24060:	mov	rax, qword ptr [r15] 	3
0x24063:	lea	rcx, [r8 + 8] 	4
0x24067:	and	rcx, 0xfffffffffffffff8 	4
0x2406b:	mov	qword ptr [r8], rax 	3
0x2406e:	mov	eax, ebp 	2
0x24070:	mov	rdx, qword ptr [r15 + rax - 8] 	5
0x24075:	mov	qword ptr [r8 + rax - 8], rdx 	5
0x2407a:	mov	rax, r8 	3
0x2407d:	sub	rax, rcx 	3
0x24080:	sub	r15, rax 	3
0x24083:	add	eax, ebp 	2
0x24085:	and	eax, 0xfffffff8 	3
0x24088:	cmp	eax, 8 	3
0x2408b:	jb	0x23eb9 	6
			> 0x23eb9
-> 0x24091 147601 ('0x23eb9', 0)
ENTRIES REMAINING 595
0x24091:	and	eax, 0xfffffff8 	3
0x24094:	xor	edx, edx 	2
0x24096:	mov	esi, edx 	2
0x24098:	add	edx, 8 	3
0x2409b:	mov	rdi, qword ptr [r15 + rsi] 	4
0x2409f:	mov	qword ptr [rcx + rsi], rdi 	4
0x240a3:	cmp	edx, eax 	2
0x240a5:	jb	0x24096 	2
			> 0x24096
-> 0x240a7 147623 ('0x24096', 0)
ENTRIES REMAINING 596
ENTRIES REMAINING 595
0x240a7:	jmp	0x23eb9 	5
0x23eb9
ENTRIES REMAINING 595
ENTRIES REMAINING 594
ENTRIES REMAINING 593
ENTRIES REMAINING 592
ENTRIES REMAINING 591
0x240f2:	jmp	0x23a2f 	5

0x25873:	cmp	eax, 3 	3
0x25876:	jne	0x258a8 	2
			> 0x258a8
-> 0x25878 153720 ('0x258a8', 0)
ENTRIES REMAINING 252
ENTRIES REMAINING 251
ENTRIES REMAINING 250
ENTRIES REMAINING 249
ENTRIES REMAINING 248
ENTRIES REMAINING 247
ENTRIES REMAINING 246
ENTRIES REMAINING 245
ENTRIES REMAINING 244
ENTRIES REMAINING 243
ENTRIES REMAINING 242
ENTRIES REMAINING 241
ENTRIES REMAINING 240
ENTRIES REMAINING 239
0x25922:	jmp	0x259a2 	2
0x259a2
ENTRIES REMAINING 239
ENTRIES REMAINING 238
ENTRIES REMAINING 237
ENTRIES REMAINING 236
ENTRIES REMAINING 235
ENTRIES REMAINING 234
ENTRIES REMAINING 233
0x25949:	lea	rdx, [r11 + r14] 	4
0x2594d:	add	rsi, rax 	3
0x25950:	jmp	0x25965 	2
0x25965
ENTRIES REMAINING 233
ENTRIES REMAINING 232
ENTRIES REMAINING 231
ENTRIES REMAINING 230
0x2596f:	movabs	rdi, 0x20000002b 	10
0x25979:	bt	rdi, rax 	4
0x2597d:	jae	0x25958 	2
			> 0x25958
-> 0x2597f 153983 ('0x25958', 0)
ENTRIES REMAINING 231
ENTRIES REMAINING 230
ENTRIES REMAINING 229
ENTRIES REMAINING 228
ENTRIES REMAININ

0x15237:	cmp	eax, 0x61 	3
0x1523a:	je	0x15248 	2
			> 0x15248
-> 0x1523c 86588 ('0x15248', 0)
ENTRIES REMAINING 200
ENTRIES REMAINING 199
0x166a9:	cmp	dword ptr [rbp - 0x170], 3 	7
0x166b0:	je	0x166db 	2
			> 0x166db
-> 0x166b2 91826 ('0x166db', 0)
ENTRIES REMAINING 200
ENTRIES REMAINING 199
ENTRIES REMAINING 198
ENTRIES REMAINING 197
ENTRIES REMAINING 196
ENTRIES REMAINING 195
0x16b42:	jmp	0x16e18 	5
0x16e18
ENTRIES REMAINING 195
ENTRIES REMAINING 194
ENTRIES REMAINING 193
ENTRIES REMAINING 192
ENTRIES REMAINING 191
ENTRIES REMAINING 190
ENTRIES REMAINING 189
ENTRIES REMAINING 188
ENTRIES REMAINING 187
ENTRIES REMAINING 186
ENTRIES REMAINING 185
ENTRIES REMAINING 184
0x1a6eb:	cmp	eax, 0x20 	3
0x1a6ee:	je	0x1a706 	2
			> 0x1a706
-> 0x1a6f0 108272 ('0x1a706', 0)
ENTRIES REMAINING 185
ENTRIES REMAINING 184
ENTRIES REMAINING 183
ENTRIES REMAINING 182
ENTRIES REMAINING 181
0x1b9ed:	cmp	eax, 2 	3
0x1b9f0:	je	0x1ba11 	2
			> 0x1ba11
-> 0x1b9f2 113138 ('0x1ba11', 0)
ENTRIES REMAINING 182
ENTR

0x1523c:	cmp	eax, 0x6f 	3
0x1523f:	jne	0x1527a 	2
			> 0x1527a
-> 0x15241 86593 ('0x1527a', 0)
ENTRIES REMAINING 66
ENTRIES REMAINING 65
0x166b2:	cmp	dword ptr [rbp - 0x170], 3 	7
0x166b9:	jg	0x166ef 	2
			> 0x166ef
-> 0x166bb 91835 ('0x166ef', 0)
ENTRIES REMAINING 66
ENTRIES REMAINING 65
ENTRIES REMAINING 64
0x1a6f0:	cmp	eax, 0x20 	3
0x1a6f3:	jg	0x1a7f5 	6
			> 0x1a7f5
-> 0x1a6f9 108281 ('0x1a7f5', 0)
ENTRIES REMAINING 65
ENTRIES REMAINING 64
0x1b9f2:	cmp	eax, 2 	3
0x1b9f5:	jg	0x1bbaa 	6
			> 0x1bbaa
-> 0x1b9fb 113147 ('0x1bbaa', 0)
ENTRIES REMAINING 65
ENTRIES REMAINING 64
0x1bc06:	cmp	eax, 2 	3
0x1bc09:	jg	0x1bebb 	6
			> 0x1bebb
-> 0x1bc0f 113679 ('0x1bebb', 0)
ENTRIES REMAINING 65
ENTRIES REMAINING 64
0x1d5dc:	cmp	dword ptr [rbp - 4], 0 	4
0x1d5e0:	jg	0x1d5fd 	2
			> 0x1d5fd
-> 0x1d5e2 120290 ('0x1d5fd', 0)
ENTRIES REMAINING 65
0x1d5e4:	cmp	dword ptr [rbp - 4], 0xb 	4
0x1d5e8:	je	0x1d61d 	2
			> 0x1d61d
-> 0x1d5ea 120298 ('0x1d61d', 0)
ENTRIES REMAINING 66
0x1e301:	cmp	dword ptr [

0x14706:	jmp	0x14730 	2
0x14730
ENTRIES REMAINING 20
ENTRIES REMAINING 19
ENTRIES REMAINING 18
ENTRIES REMAINING 17
ENTRIES REMAINING 16
ENTRIES REMAINING 15
ENTRIES REMAINING 14
ENTRIES REMAINING 13
0x1bc20:	jmp	0x1bc23 	2
0x1bc23
ENTRIES REMAINING 13
ENTRIES REMAINING 12
ENTRIES REMAINING 11
ENTRIES REMAINING 10
ENTRIES REMAINING 9
ENTRIES REMAINING 8
0x21654:	jmp	0x216a6 	2
0x216a6
ENTRIES REMAINING 8
ENTRIES REMAINING 7
ENTRIES REMAINING 6
ENTRIES REMAINING 5
ENTRIES REMAINING 4
ENTRIES REMAINING 3
ENTRIES REMAINING 2
ENTRIES REMAINING 1


In [5]:

addresses = list(address_and_instructions.keys())
addresses.sort()
sorted_address_and_instructions = {i: address_and_instructions[i] for i in addresses}

predicted_address = list(sorted_address_and_instructions.keys())[0]

with open('./data/instruction_clusters.txt', 'w') as data_file:
    for address, inst in sorted_address_and_instructions.items():
        
        print(address, inst.address, inst.mnemonic, inst.op_str ,'     >>  ',inst.size)
        
        if inst.address!=predicted_address:
            data_file.write('\n')
        
        data_file.write(inst.mnemonic+" "+inst.op_str+";")
        predicted_address = inst.address + inst.size

        


20192 20192 call 0x4810      >>   5
20197 20197 nop word ptr cs:[rax + rax]      >>   10
20207 20207 nop       >>   1
20208 20208 endbr64       >>   4
20212 20212 xor ebp, ebp      >>   2
20214 20214 mov r9, rdx      >>   3
20217 20217 pop rsi      >>   1
20218 20218 mov rdx, rsp      >>   3
20221 20221 and rsp, 0xfffffffffffffff0      >>   4
20225 20225 push rax      >>   1
20226 20226 push rsp      >>   1
20227 20227 xor r8d, r8d      >>   3
20230 20230 xor ecx, ecx      >>   2
20232 20232 lea rdi, [rip + 0x28fb]      >>   7
20239 20239 call qword ptr [rip + 0x2a0a3]      >>   6
20441 20441 endbr64       >>   4
20445 20445 push rbp      >>   1
20446 20446 mov rbp, rsp      >>   3
20449 20449 mov eax, dword ptr [rip + 0x2b9f5]      >>   6
20455 20455 cmp eax, 6      >>   3
20458 20458 jle 0x501a      >>   2
20460 20460 mov eax, dword ptr [rip + 0x2a036]      >>   6
20466 20466 test eax, eax      >>   2
20468 20468 je 0x5008      >>   2
20470 20470 mov eax, dword ptr [rip + 0x2b9e4]   

50503 50503 mov esi, edx      >>   2
50505 50505 mov rdi, rax      >>   3
50508 50508 call 0xb706      >>   5
50513 50513 lea rax, [rip + 0x24d68]      >>   7
50520 50520 mov rdi, rax      >>   3
50523 50523 call 0x4960      >>   5
50528 50528 mov esi, eax      >>   2
50530 50530 lea rax, [rip + 0x24d57]      >>   7
50537 50537 mov rdi, rax      >>   3
50540 50540 call 0xb706      >>   5
50545 50545 mov rax, qword ptr [rbp - 0x18]      >>   4
50549 50549 mov rdi, rax      >>   3
50552 50552 call 0x4960      >>   5
50557 50557 mov edx, eax      >>   2
50559 50559 mov rax, qword ptr [rbp - 0x18]      >>   4
50563 50563 mov esi, edx      >>   2
50565 50565 mov rdi, rax      >>   3
50568 50568 call 0xb706      >>   5
50573 50573 mov eax, 0      >>   5
50578 50578 call 0xb4b7      >>   5
50583 50583 lea rax, [rbp - 0x21]      >>   4
50587 50587 mov rdi, rax      >>   3
50590 50590 call 0xc067      >>   5
50595 50595 nop       >>   1
50596 50596 mov rax, qword ptr [rbp - 8]      >>   4
50600

52527 52527 mov eax, 0      >>   5
52532 52532 call 0xb8a5      >>   5
52537 52537 mov rax, qword ptr [rip + 0x23ca8]      >>   7
52544 52544 movzx eax, byte ptr [rax + 8]      >>   4
52548 52548 mov byte ptr [rbp - 0x28], al      >>   3
52551 52551 mov rax, qword ptr [rip + 0x23c9a]      >>   7
52558 52558 movzx eax, byte ptr [rax + 9]      >>   4
52562 52562 mov byte ptr [rbp - 0x27], al      >>   3
52565 52565 mov edx, dword ptr [rbp - 0x3c]      >>   3
52568 52568 lea rax, [rbp - 0x30]      >>   4
52572 52572 mov esi, edx      >>   2
52574 52574 mov rdi, rax      >>   3
52577 52577 mov eax, 0      >>   5
52582 52582 call 0x4d30      >>   5
52587 52587 mov dword ptr [rbp - 0x40], eax      >>   3
52590 52590 cmp dword ptr [rbp - 0x40], -1      >>   4
52594 52594 je 0xcdd8      >>   2
52596 52596 nop       >>   1
52597 52597 jmp 0xcd78      >>   2
52599 52599 nop       >>   1
52600 52600 mov edx, dword ptr [rip + 0x23c5e]      >>   6
52606 52606 mov eax, dword ptr [rip + 0x23c5c]     

67928 67928 mov dword ptr [rax + 0x2c], 0      >>   7
67935 67935 mov rax, qword ptr [rbp - 8]      >>   4
67939 67939 mov dword ptr [rax + 0x14], 0x3fffffff      >>   7
67946 67946 mov rax, qword ptr [rbp - 8]      >>   4
67950 67950 mov qword ptr [rax + 0x20], 0      >>   8
67958 67958 mov rax, qword ptr [rbp - 8]      >>   4
67962 67962 mov qword ptr [rax], 0      >>   7
67969 67969 mov rax, qword ptr [rbp - 8]      >>   4
67973 67973 mov qword ptr [rax + 0x48], 0      >>   8
67981 67981 mov rax, qword ptr [rbp - 8]      >>   4
67985 67985 mov byte ptr [rax + 0x6d], 1      >>   4
67989 67989 mov rax, qword ptr [rbp - 8]      >>   4
67993 67993 mov dword ptr [rax + 0x88], 1      >>   10
68003 68003 mov rax, qword ptr [rbp - 8]      >>   4
68007 68007 mov dword ptr [rax + 0x8c], 0      >>   10
68017 68017 mov rax, qword ptr [rbp - 8]      >>   4
68021 68021 mov dword ptr [rax + 0x74], 0      >>   7
68028 68028 mov rax, qword ptr [rbp - 8]      >>   4
68032 68032 mov dword ptr [rax + 0

94481 94481 cmp dword ptr [rbp - 0x5c], 2      >>   4
94485 94485 je 0x17158      >>   2
94487 94487 mov eax, dword ptr [rbp - 0x5c]      >>   3
94490 94490 sub eax, 1      >>   3
94493 94493 cdqe       >>   2
94495 94495 lea rdx, [rax*8]      >>   8
94503 94503 lea rax, [rip + 0x19452]      >>   7
94510 94510 mov rdx, qword ptr [rdx + rax]      >>   4
94514 94514 mov rax, qword ptr [rbp - 0x38]      >>   4
94518 94518 mov r8d, 0x1e      >>   6
94524 94524 mov ecx, 0      >>   5
94529 94529 mov rsi, rax      >>   3
94532 94532 lea rax, [rip + 0x117c0]      >>   7
94539 94539 mov rdi, rax      >>   3
94542 94542 mov eax, 0      >>   5
94547 94547 call 0x115fd      >>   5
94552 94552 mov eax, 0      >>   5
94557 94557 call 0x10857      >>   5
94562 94562 mov rax, qword ptr [rbp - 0x78]      >>   4
94566 94566 mov rdi, rax      >>   3
94569 94569 mov eax, 0      >>   5
94574 94574 call 0x13506      >>   5
94579 94579 mov rax, qword ptr [rbp - 0x80]      >>   4
94583 94583 mov rdi, rax    

98135 98135 mov rax, qword ptr [rax + 0x18]      >>   4
98139 98139 mov rdi, rax      >>   3
98142 98142 call 0x4960      >>   5
98147 98147 mov rdx, qword ptr [rbp - 0x38]      >>   4
98151 98151 add rax, rdx      >>   3
98154 98154 mov rdi, rax      >>   3
98157 98157 call 0x24650      >>   5
98162 98162 mov qword ptr [rbp - 0x18], rax      >>   4
98166 98166 mov rax, qword ptr [rbp - 0x70]      >>   4
98170 98170 mov rdx, qword ptr [rax + 0x18]      >>   4
98174 98174 mov rcx, qword ptr [rbp - 0x28]      >>   4
98178 98178 mov rax, qword ptr [rbp - 0x18]      >>   4
98182 98182 lea rsi, [rip + 0x10842]      >>   7
98189 98189 mov rdi, rax      >>   3
98192 98192 mov eax, 0      >>   5
98197 98197 call 0x4dd0      >>   5
98202 98202 mov rcx, qword ptr [rip + 0x19667]      >>   7
98209 98209 mov rdx, qword ptr [rbp - 0x18]      >>   4
98213 98213 lea rsi, [rbp - 0x40]      >>   4
98217 98217 mov rax, qword ptr [rbp - 0x20]      >>   4
98221 98221 mov rdi, rax      >>   3
98224 98224 c

116929 116929 call 0x4ec0      >>   5
116934 116934 mov rdx, qword ptr [rax]      >>   3
116937 116937 mov rax, qword ptr [rbp - 0x8c8]      >>   7
116944 116944 movzx eax, byte ptr [rax]      >>   3
116947 116947 movsx rax, al      >>   4
116951 116951 add rax, rax      >>   3
116954 116954 add rax, rdx      >>   3
116957 116957 movzx eax, word ptr [rax]      >>   3
116960 116960 movzx eax, ax      >>   3
116963 116963 and eax, 0x2000      >>   5
116968 116968 test eax, eax      >>   2
116970 116970 jne 0x1c8ab      >>   2
116972 116972 mov rax, qword ptr [rbp - 0x8c8]      >>   7
116979 116979 movzx eax, byte ptr [rax]      >>   3
116982 116982 test al, al      >>   2
116984 116984 je 0x1c924      >>   2
116986 116986 mov dword ptr [rbp - 0x8cc], 1      >>   10
116996 116996 mov rax, qword ptr [rbp - 0x8c8]      >>   7
117003 117003 mov esi, 0x52      >>   5
117008 117008 mov rdi, rax      >>   3
117011 117011 call 0x49b0      >>   5
117016 117016 test rax, rax      >>   3
117019 117

125600 125600 je 0x1ead6      >>   2
125602 125602 mov eax, 0      >>   5
125607 125607 call 0xc083      >>   5
125612 125612 mov eax, 0      >>   5
125617 125617 call 0xb099      >>   5
125622 125622 mov edi, 0x1c      >>   5
125627 125627 call 0x5367      >>   5
125632 125632 mov dword ptr [rip + 0x12ffe], 0      >>   10
125642 125642 mov dword ptr [rip + 0x12ff8], 0      >>   10
125652 125652 jmp 0x1eaeb      >>   2
125654 125654 mov eax, dword ptr [rip + 0x12ff0]      >>   6
125660 125660 test eax, eax      >>   2
125662 125662 je 0x1eaeb      >>   2
125664 125664 mov dword ptr [rip + 0x12fe2], 0      >>   10
125674 125674 nop       >>   1
125675 125675 pop rbp      >>   1
125676 125676 ret       >>   1
125677 125677 endbr64       >>   4
125681 125681 push rbp      >>   1
125682 125682 mov rbp, rsp      >>   3
125685 125685 sub rsp, 0x10      >>   4
125689 125689 mov dword ptr [rbp - 4], edi      >>   3
125692 125692 mov eax, dword ptr [rbp - 4]      >>   3
125695 125695 mov dword 

142784 142784 leave       >>   1
142786 142786 endbr64       >>   4
142790 142790 push rbp      >>   1
142791 142791 mov rbp, rsp      >>   3
142794 142794 push r12      >>   2
142796 142796 push rbx      >>   1
142797 142797 sub rsp, 0x30      >>   4
142801 142801 mov dword ptr [rbp - 0x34], edi      >>   3
142804 142804 mov dword ptr [rbp - 0x38], esi      >>   3
142807 142807 mov qword ptr [rbp - 0x40], rdx      >>   4
142811 142811 mov qword ptr [rbp - 0x20], 0      >>   8
142819 142819 mov dword ptr [rbp - 0x28], 0      >>   7
142826 142826 mov dword ptr [rbp - 0x24], 0      >>   7
142833 142833 mov rax, qword ptr [rbp - 0x40]      >>   4
142837 142837 mov rdi, rax      >>   3
142840 142840 mov eax, 0      >>   5
142845 142845 call 0x22fd3      >>   5
142850 142850 mov qword ptr [rbp - 0x18], rax      >>   4
142854 142854 cmp qword ptr [rbp - 0x18], 0      >>   5
142859 142859 jne 0x22e17      >>   2
142861 142861 mov eax, 0      >>   5
142866 142866 jmp 0x22fca      >>   5
142871

146174 146174 nop       >>   2
146176 146176 fstp xword ptr [rsp + 0x20]      >>   4
146180 146180 sub rsp, 0x10      >>   4
146184 146184 mov esi, 1      >>   5
146189 146189 xor eax, eax      >>   2
146191 146191 mov r12, qword ptr [rsp + 0x10]      >>   5
146196 146196 lea rcx, [rip + 0x5afd]      >>   7
146203 146203 mov rdx, -1      >>   7
146210 146210 mov rdi, r12      >>   3
146213 146213 fstp xword ptr [rsp]      >>   3
146216 146216 call 0x4ed0      >>   5
146221 146221 mov rdi, r12      >>   3
146224 146224 call 0x4960      >>   5
146229 146229 mov rdx, rax      >>   3
146232 146232 pop rax      >>   1
146233 146233 pop rcx      >>   1
146234 146234 fld xword ptr [rsp + 0x20]      >>   4
146238 146238 cmp rdx, rbp      >>   3
146241 146241 ja 0x23d00      >>   6
146247 146247 test byte ptr [rsp + 0x48], 8      >>   5
146252 146252 je 0x23b68      >>   2
146254 146254 mov rax, qword ptr [rsp]      >>   4
146258 146258 cmp byte ptr [rax + rdx - 1], 0x30      >>   5
146263 1462

In [6]:
data_dir_path = "./data/binaries/"
dir_file_list = os.listdir(data_dir_path)

['gitwipe',
 'gitwhich',
 'gitview',
 'main.out',
 'gitfm',
 'gitps',
 'gitkeys',
 'array',
 'main_d4.out']